In [2]:
import xlsxwriter

In [3]:
from repytex.worksheets.worksheet import pull_datas
from repytex.reports.eval import pull_datas as pull_sqlite
import pandas as pd
import numpy as np
import sqlite3

In [4]:
conn = sqlite3.connect('./recopytex.db')

# to xlxs

In [4]:
datas = pull_datas(1, conn)
datas

{'evaluation':    id               name  term  t_id
 0   1  DS1 mise en jambe     1     1,
 'exercises':    id                        name  eval_id                        date comment
 0   1  1 - Prendre la température        1  2017-09-05 00:00:00.000000        
 1   2             2 - Maladroite!        1  2017-09-05 00:00:00.000000        ,
 'question_scores':       id  question_id  student_id value
 0      1            1           1     1
 1      2            2           1     2
 2      3            3           1     .
 3      4            1           2     2
 4      5            2           2     2
 5      6            3           2     1
 6      7            1           3     3
 7      8            2           3     0
 8      9            3           3     0
 9     10            1           4     3
 10    11            2           4     3
 11    12            3           4     0
 12    13            1           5     1
 13    14            2           5     2
 14    15            

In [5]:
datas['evaluation']["name"][0]

'DS1 mise en jambe'

In [6]:
q_df = datas["questions"]
q_df = q_df.assign(
    Nom = q_df[["name", "comment"]].apply(lambda x: " ".join(x), 1)
)

In [7]:
q_df.head()

id name  score_rate  is_leveled  exercise_id competence       domain  \
0   1    1           0           1            1       Cher    Grandeurs   
1   2    2           0           1            1        Cal    Grandeurs   
2   3  2.c           0           1            1        Cal    Grandeurs   
0   4                0           1            2       Cher  4opérations   
1   5                0           1            2       Cher  4opérations   

                             comment                                    Nom  
0             Lecture du thermomètre               1 Lecture du thermomètre  
1        Suivre programme de calculs          2 Suivre programme de calculs  
2  Renverser un programme de calculs  2.c Renverser un programme de calculs  
0    Lire le tableau et le graphique        Lire le tableau et le graphique  
1             Décomposer le problème                 Décomposer le problème

In [8]:
datas["exercises"]

id                        name  eval_id                        date comment
0   1  1 - Prendre la température        1  2017-09-05 00:00:00.000000        
1   2             2 - Maladroite!        1  2017-09-05 00:00:00.000000

In [9]:
ex_q = q_df.groupby("exercise_id")\
    .agg({"score_rate": np.sum, "competence": lambda x: '-'.join(list(x))}) \
    .merge(datas["exercises"], left_index=True, right_on='id')
ex_q = ex_q.assign(
    Nom = ex_q["name"].apply(lambda x: f"Ex {x}"),
    exercise_id = ex_q["id"]
)
#ex_q

In [10]:
sel_fields = ['Nom', 'competence', 'score_rate', 'exercise_id']
xls_df = pd.concat([ex_q[sel_fields], q_df[sel_fields]]).sort_values("exercise_id")
#xls_df

In [11]:
#writer = pd.ExcelWriter("./test.xlsx", engine="xlsxwriter")
#xls_df.to_excel(writer, index=False, sheet_name='DNB blanc 2')

In [12]:
#workbook = writer.book
#worksheet = writer.sheets['DNB blanc 2']

In [13]:
#first_line_format = workbook.add_format({"align": 'center', "rotation":90})

#worksheet.set_column('A:D', 20)


In [14]:
#writer.save()

## From xlsx

In [9]:
df = pd.read_excel("./DNB_blanc2/DNB2_302.xlsx")
df.head()

competence  Barème  ABDALLAH ALAOUI Taiassima  \
DNB blanc 2 général                NaN     112                         24   
Ex 1 - Programme de calculs        NaN      15                          3   
1 et 2 Suivre le programme         Cal       6                          3   
3 Renverser le programme           Rai       3                          0   
4 Toujours la même chose           Rai       3                          0   

                             ADANI Ismou  AHAMADA Dhoulkamal  \
DNB blanc 2 général                 52.0                46.5   
Ex 1 - Programme de calculs         11.0                 3.0   
1 et 2 Suivre le programme           6.0                 2.0   
3 Renverser le programme             3.0                 0.0   
4 Toujours la même chose             2.0                 0.0   

                             AHAMADI Asbahati  AHAMADI OUSSENI Ansufidine  \
DNB blanc 2 général                        65                        27.0   
Ex 1 - Programme de calculs                 0                         1.0   
1 et 2 Suivre le programme                  0                         0.0   
3 Renverser le programme                    0                         0.0   
4 Toujours la même chose                    0                         0.0   

                             AHAMED Fayadhi  AHMED SAID Hadaita  \
DNB blanc 2 général                    25.5                  75   
Ex 1 - Programme de calculs             0.0                   3   
1 et 2 Suivre le programme              0.0                   2   
3 Renverser le programme                0.0                   0   
4 Toujours la même chose                0.0                   0   

                             ALI MADI Anissa  ...   MOUSSRI Bakari  \
DNB blanc 2 général                       72  ...               40   
Ex 1 - Programme de calculs               10  ...                2   
1 et 2 Suivre le programme                 6  ...                0   
3 Renverser le programme                   0  ...                0   
4 Toujours la même chose                   3  ...                0   

                             SAID Ftoumia  ZAKOTRA Claudian  TOUFAIL Salahou  \
DNB blanc 2 général                    50                60             58.5   
Ex 1 - Programme de calculs             0                 7              2.0   
1 et 2 Suivre le programme              0                 2              1.0   
3 Renverser le programme                0                 2              0.0   
4 Toujours la même chose                0                 0              0.0   

                               moyenne  Min      Q1     ME      Q3   Max  
DNB blanc 2 général          43.403846   21  27.125  41.25  56.875  75.0  
Ex 1 - Programme de calculs   4.019231    0   1.250   3.00   6.875  11.0  
1 et 2 Suivre le programme    2.692308    0   0.250   2.00   5.750   6.0  
3 Renverser le programme      0.596154    0   0.000   0.00   1.125   3.0  
4 Toujours la même chose      0.192308    0   0.000   0.00   0.000   3.0  

[5 rows x 35 columns]

On enlève les colonnes inutiles et on format les prénoms

In [10]:
import unicodedata
def normalize_str(s):
    return unicodedata.normalize('NFD', s).encode('ascii', 'ignore').lower()

In [13]:
df = df.drop(['competence', 'Barème','moyenne',
       'Min', 'Q1', 'ME', 'Q3', 'Max'], 1)
df.columns = [normalize_str(i) for i in df.columns]
df.head()

b'abdallah alaoui taiassima'  b'adani ismou'  \
DNB blanc 2 général                                    24            52.0   
Ex 1 - Programme de calculs                             3            11.0   
1 et 2 Suivre le programme                              3             6.0   
3 Renverser le programme                                0             3.0   
4 Toujours la même chose                                0             2.0   

                             b'ahamada dhoulkamal'  b'ahamadi asbahati'  \
DNB blanc 2 général                           46.5                   65   
Ex 1 - Programme de calculs                    3.0                    0   
1 et 2 Suivre le programme                     2.0                    0   
3 Renverser le programme                       0.0                    0   
4 Toujours la même chose                       0.0                    0   

                             b'ahamadi ousseni ansufidine'  b'ahamed fayadhi'  \
DNB blanc 2 général                                   27.0               25.5   
Ex 1 - Programme de calculs                            1.0                0.0   
1 et 2 Suivre le programme                             0.0                0.0   
3 Renverser le programme                               0.0                0.0   
4 Toujours la même chose                               0.0                0.0   

                             b'ahmed said hadaita'  b'ali madi anissa'  \
DNB blanc 2 général                             75                  72   
Ex 1 - Programme de calculs                      3                  10   
1 et 2 Suivre le programme                       2                   6   
3 Renverser le programme                         0                   0   
4 Toujours la même chose                         0                   3   

                             b'ali raydel'  b'attoumane ali fatima'  \
DNB blanc 2 général                   45.5                     26.0   
Ex 1 - Programme de calculs            9.0                      6.5   
1 et 2 Suivre le programme             6.0                      5.0   
3 Renverser le programme               3.0                      1.5   
4 Toujours la même chose               0.0                      0.0   

                                    ...          b'hamedaly doulkifly'  \
DNB blanc 2 général                 ...                           23.5   
Ex 1 - Programme de calculs         ...                            2.0   
1 et 2 Suivre le programme          ...                            2.0   
3 Renverser le programme            ...                            0.0   
4 Toujours la même chose            ...                            0.0   

                             b'ibrahim chaharzade'  b'ibrahim nassur'  \
DNB blanc 2 général                           49.0               42.5   
Ex 1 - Programme de calculs                    4.5                7.5   
1 et 2 Suivre le programme                     3.0                6.0   
3 Renverser le programme                       0.0                1.5   
4 Toujours la même chose                       0.0                0.0   

                             b'inoussa anchoura'  b'mohamed nadia'  \
DNB blanc 2 général                          NaN              27.5   
Ex 1 - Programme de calculs                  NaN               2.5   
1 et 2 Suivre le programme                   NaN               1.0   
3 Renverser le programme                     NaN               0.0   
4 Toujours la même chose                     NaN               0.0   

                             b'mouhoudhoire izak'  b'moussri bakari'  \
DNB blanc 2 général                            37                 40   
Ex 1 - Programme de calculs                     5                  2   
1 et 2 Suivre le programme                      4                  0   
3 Renverser le programme                        0                  0   
4 Toujours la même chose                        0                  0   

                  

On enlèves les lignes calculées par excel pour ne garder que les données

In [15]:
df = df[list(~df.reset_index()["index"].apply(lambda x: x.startswith("Ex") or x.startswith("DNB")))]
df

b'abdallah alaoui taiassima'  \
1 et 2 Suivre le programme                                         3   
3 Renverser le programme                                           0   
4 Toujours la même chose                                           0   
4 Développer F                                                     0   
1 Fraction réponse                                                 4   
1 Notation et vocabulaire                                          6   
2 Arbre de probabilité                                             0   
1 et 2 Raisonnement pour choisir                                   2   
1 et 2 Décomposer le problème                                      2   
1 et 2 Choix des opérations et calculs                             0   
3 Composition des réductions                                       0   
1 Logique de la réponse                                            0   
1 Calculs des indicateurs                                          0   
1 Clarté des explications                                          0   
2 Calculs                                                          0   
2 Validité des réponses                                            0   
2 Tests des possibilités                                           0   
 Reconnaitre les théorèmes                                         2   
 Validité des calculs                                              0   
 Suivi du raisonnement géométrique                                 0   
1 Quantité de sucre                                                0   
2 Calcul du volume                                                 0   
2 Nombre de pots                                                   0   
3 Dessin de l'étiquette                                            0   
3 Mise à l'echelle                                                 0   
3 Longueur de l'étiquette                                          0   

                                        b'adani ismou'  b'ahamada dhoulkamal'  \
1 et 2 Suivre le programme                         6.0                    2.0   
3 Renverser le programme                           3.0                    0.0   
4 Toujours la même chose                           2.0                    0.0   
4 Développer F                                     0.0                    1.0   
1 Fraction réponse                                 4.0                    4.0   
1 Notation et vocabulaire                          0.0                    6.0   
2 Arbre de probabilité                             0.0                    0.0   
1 et 2 Raisonnement pour choisir                   1.0                    3.0   
1 et 2 Décomposer le problème                      2.0                    3.0   
1 et 2 Choix des opérations et calculs             1.0                    0.0   
3 Composition des réductions                       0.0                    1.0   
1 Logique de la réponse                            3.0                    3.0   
1 Calculs des indicateurs                          2.0                    3.0   
1 Clarté des explications                          1.0                    3.0   
2 Calculs                                          1.5                    0.0   
2 Validité des réponses                            1.5                    1.5   
2 Tests des possibilités                           0.0                    0.0   
 Reconnaitre les théorèmes                         2.0                    4.0   
 Validité des calculs                              0.0                    3.0   
 Suivi du raisonnement géométrique                 0.0                    1.0   
1 Quantité de sucre                                0.0                    0.0   
2 Calcul du volume                                 0.0                    1.0   
2 Nombre de pots                                   0.0                    0.0   
3 Dessin de l'étiquette                            0.0                    0.0   
3 Mise à l'echelle                                 0.0                

In [16]:
df = df.reset_index()
df.head()

index  b'abdallah alaoui taiassima'  b'adani ismou'  \
0  1 et 2 Suivre le programme                             3             6.0   
1    3 Renverser le programme                             0             3.0   
2    4 Toujours la même chose                             0             2.0   
3              4 Développer F                             0             0.0   
4          1 Fraction réponse                             4             4.0   

   b'ahamada dhoulkamal'  b'ahamadi asbahati'  b'ahamadi ousseni ansufidine'  \
0                    2.0                    0                            0.0   
1                    0.0                    0                            0.0   
2                    0.0                    0                            0.0   
3                    1.0                    0                            1.0   
4                    4.0                    4                            3.0   

   b'ahamed fayadhi'  b'ahmed said hadaita'  b'ali madi anissa'  \
0                0.0                      2                   6   
1                0.0                      0                   0   
2                0.0                      0                   3   
3                0.0                      1                   1   
4                4.0                      4                   4   

   b'ali raydel'         ...          b'hamedaly doulkifly'  \
0            6.0         ...                            2.0   
1            3.0         ...                            0.0   
2            0.0         ...                            0.0   
3            0.0         ...                            0.0   
4            4.0         ...                            3.0   

   b'ibrahim chaharzade'  b'ibrahim nassur'  b'inoussa anchoura'  \
0                    3.0                6.0                  NaN   
1                    0.0                1.5                  NaN   
2                    0.0                0.0                  NaN   
3                    1.5                0.0                  NaN   
4                    4.0                4.0                  NaN   

   b'mohamed nadia'  b'mouhoudhoire izak'  b'moussri bakari'  b'said ftoumia'  \
0               1.0                     4                  0                0   
1               0.0                     0                  0                0   
2               0.0                     0                  0                0   
3               1.5                     1                  2                0   
4               4.0                     4                  4                4   

   b'zakotra claudian'  b'toufail salahou'  
0                    2                 1.0  
1                    2                 0.0  
2                    0                 0.0  
3                    3                 1.0  
4                    4                 4.0  

[5 rows x 28 columns]

In [18]:
df = df.assign(
    q_name = df["index"].apply(lambda x: x.split(" ")[0]),
    q_comment = df["index"].apply(lambda x: " ".join(x.split(" ")[1:])),
        )
df

index  b'abdallah alaoui taiassima'  \
0               1 et 2 Suivre le programme                             3   
1                 3 Renverser le programme                             0   
2                 4 Toujours la même chose                             0   
3                           4 Développer F                             0   
4                       1 Fraction réponse                             4   
5                1 Notation et vocabulaire                             6   
6                   2 Arbre de probabilité                             0   
7         1 et 2 Raisonnement pour choisir                             2   
8            1 et 2 Décomposer le problème                             2   
9   1 et 2 Choix des opérations et calculs                             0   
10            3 Composition des réductions                             0   
11                 1 Logique de la réponse                             0   
12               1 Calculs des indicateurs                             0   
13               1 Clarté des explications                             0   
14                               2 Calculs                             0   
15                 2 Validité des réponses                             0   
16                2 Tests des possibilités                             0   
17               Reconnaitre les théorèmes                             2   
18                    Validité des calculs                             0   
19       Suivi du raisonnement géométrique                             0   
20                     1 Quantité de sucre                             0   
21                      2 Calcul du volume                             0   
22                        2 Nombre de pots                             0   
23                 3 Dessin de l'étiquette                             0   
24                      3 Mise à l'echelle                             0   
25               3 Longueur de l'étiquette                             0   

    b'adani ismou'  b'ahamada dhoulkamal'  b'ahamadi asbahati'  \
0              6.0                    2.0                    0   
1              3.0                    0.0                    0   
2              2.0                    0.0                    0   
3              0.0                    1.0                    0   
4              4.0                    4.0                    4   
5              0.0                    6.0                    8   
6              0.0                    0.0                    0   
7              1.0                    3.0                    5   
8              2.0                    3.0                    5   
9              1.0                    0.0                    2   
10             0.0                    1.0                    1   
11             3.0                    3.0                    3   
12             2.0                    3.0                    3   
13             1.0                    3.0                    3   
14             1.5                    0.0                    3   
15             1.5                    1.5                    3   
16             0.0                    0.0                    3   
17             2.0                    4.0                    3   
18             0.0                    3.0                    3   
19             0.0                    1.0                    3   
20             0.0                    0.0                    3   
21             0.0                    1.0                    0   
22             0.0                    0.0                    0   
23             0.0                    0.0                    0   
24             0.0                    0.0                    0   
25             0.0                    0.0                    0   

    b'ahamadi ousseni ansufidine'  b'ahamed fayadhi'  b'ahmed said hadaita'  \
0                             0.0                0.0                      2   
1                             0.0          

In [19]:
df = df.set_index(["index", "q_name", "q_comment"]).stack().reset_index()
df.head()

index q_name                 q_comment  \
0  1 et 2 Suivre le programme      1  et 2 Suivre le programme   
1  1 et 2 Suivre le programme      1  et 2 Suivre le programme   
2  1 et 2 Suivre le programme      1  et 2 Suivre le programme   
3  1 et 2 Suivre le programme      1  et 2 Suivre le programme   
4  1 et 2 Suivre le programme      1  et 2 Suivre le programme   

                         level_3    0  
0   b'abdallah alaoui taiassima'  3.0  
1                 b'adani ismou'  6.0  
2          b'ahamada dhoulkamal'  2.0  
3            b'ahamadi asbahati'  0.0  
4  b'ahamadi ousseni ansufidine'  0.0

In [20]:
df = df.rename(columns={0:"value", "level_3": "norm_surname"})

Il ne reste plus qu'à trouver les correspondances avec la base de données.

In [21]:
sqlite_datas = pull_sqlite(34, conn)

Les élèves

In [27]:
def tmp()
st_df = sqlite_datas["students"]
st_df = st_df.assign(
    norm_surname = st_df[["surname", "name"]].apply(lambda x: normalize_str(" ".join(x)))
)
st_df.head()

id              name      surname mail commment  tribe_id norm_surname
0   1  ABDALLAH ALLAOUI    Taiassima          None         1          NaN
1   2             ADANI        Ismou          None         1          NaN
2   3           AHAMADA   Dhoulkamal          None         1          NaN
3   4           AHAMADI     Asbahati          None         1          NaN
4   5   AHAMADI OUSSENI  Ansufiddine          None         1          NaN

In [25]:
df = pd.merge(df, st_df, left_on='norm_surname', right_on="norm_surname")[["q_comment", "id", "value"]]

In [26]:
df

Empty DataFrame
Columns: [q_comment, id, value]
Index: []

Les questions

In [26]:
q_df = sqlite_datas["questions"]
q_df.head()

id        name  score_rate  is_leveled  exercise_id competence  \
0  369           1           3           0          114        Mod   
1  370           1           3           0          114        Cal   
2  371           2           4           0          114        Rep   
0  372         1.a           3           0          115       Cher   
1  373  1.b et 2.b           3           0          115        Rep   

         domain                comment  
0     Geometrie  Reconnaitre Pythagore  
1     Geometrie                Calculs  
2     Geometrie       Calcul de l'aire  
0  Statistiques     Lecture de tableau  
1  Statistiques     Minimum et maximum

In [27]:
df = pd.merge(df, q_df, left_on="q_comment", right_on="comment")[["id_x", "id_y", "value"]]\
    .rename(columns={"id_x": "student_id", "id_y": "question_id"})

Yes ça y est je dois les avoir!

In [28]:
df.head()

student_id  question_id  value
0          27          369      3
1          28          369      0
2          29          369      3
3          30          369      3
4          32          369      1

Et maintenant on sauvegarde tout!

In [29]:
df.to_sql("score", conn, if_exists='append', index=False)

In [30]:
fdsqfdsq

NameError: name 'fdsqfdsq' is not defined

## Fait au DNB blanc 1

In [ ]:
wb = xlsxwriter.Workbook("DNB_BLANC_pro1.xlsx")

Formatages

In [ ]:
eval_format = wb.add_format({'bold': True, 'font_color': 'red'})
eval_cell = wb.add_format()
eval_cell.set_bg_color("red")
# exo_cell

La feuille de calcul

In [ ]:
wb = xlsxwriter.Workbook("DS4_302.xlsx")

In [ ]:
ws = wb.add_worksheet()

En tête du tableau

In [ ]:
ws.write(0,1,"Competence")
ws.write(0,2,"Barème")

Toutes les questions et exercices

In [ ]:
def q_line(q, row, ws):
    ws.write(row, 0, f"{q.name} - {q.comment}")
    ws.write(row, 1, f"{q.competence}")
    ws.write(row, 2, q.score_rate)

In [ ]:
def exo_block(exo, row, ws):
    qrow = row
    for q in exo["questions"]:
        qrow += 1
        q_line(q, qrow, ws)
    ws.write(row, 0, f"Ex {exo['name']}")
    row_range = ", ".join([f"C{i}" for i in range(row+2, qrow+2)])
    for i in range(30):
        ws.write(row, i+2, f"=SUM({row_range})")
    return qrow

In [ ]:
row = 2
exo_rows = []
for exo in ev.exercises:
    exo_rows.append(row)
    row = exo_block(exo, row, ws) + 1
ws.write(1,0, ev.name, eval_format)
exo_xls_range = ", ".join([f"C{i+1}" for i in exo_rows])
for i in range(30):
    ws.write(1,i+2, f"=SUM({exo_xls_range})", eval_format)

In [ ]:
wb.close()

# Avec openpyxl

In [ ]:
from openpyxl import Workbook
from openpyxl.styles import PatternFill, Border, Side, Alignment, Protection, Font, colors

In [ ]:
colors.RED

In [ ]:
wb = Workbook()

In [ ]:
ws = wb.create_sheet(ev.name)

In [ ]:
ws.cell(1,2,"Competence")
ws.cell(1,3,"Barème")

In [ ]:
def q_line(q, row, ws):
    ws.cell(row, 1, f"{q.name} - {q.comment}")
    ws.cell(row, 2, f"{q.competence}")
    ws.cell(row, 3, q.score_rate)

In [ ]:
def exo_block(exo, row, ws):
    qrow = row
    for q in exo["questions"]:
        qrow += 1
        q_line(q, qrow, ws)
    ws.cell(row, 1, f"Ex {exo['name']}")
    row_range = ", ".join([f"C{i}" for i in range(row+1, qrow+1)])
    ws.cell(row, 3, f"=SUM({row_range})")
    return qrow

In [ ]:
row = 3
exo_rows = []
for exo in ev.exercises:
    exo_rows.append(row)
    row = exo_block(exo, row, ws) + 1
eval_row = ws.row_dimensions[2]
eval_row.fill = PatternFill(bgColor=colors.RED)
ws.cell(2,1, ev.name)
exo_xls_range = ", ".join([f"C{i}" for i in exo_rows])
ws.cell(2,3, f"=SUM({exo_xls_range})")

In [ ]:
ev.tribe

In [ ]:
wb.save(f"./{ev.name}-{ev.tribe}.xlsx")